In [2]:
%pip install bertopic pandas scikit-learn


[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


In [3]:
import os  # Import the os module for file and directory operations

%pip install kagglehub
import kagglehub


[notice] A new release of pip is available: 24.3.1 -> 25.0.1
[notice] To update, run: pip install --upgrade pip
Note: you may need to restart the kernel to use updated packages.


/Users/thytran/Library/CloudStorage/OneDrive-Personal/Documents/Schools/NEU/NEU/Semesters/4. Spring25/2. Synthetic AI Group/code/venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [4]:
import pandas as pd

dataset_path = kagglehub.dataset_download("shanegerami/ai-vs-human-text")

# ✅ Find the CSV file within the downloaded dataset.
csv_file = None
for filename in os.listdir(dataset_path):
    if filename.endswith(".csv"):
        csv_file = filename
        break

if csv_file is None:
    raise FileNotFoundError(f"No CSV file found in the dataset directory: {dataset_path}")

# ✅ Construct the full path to the CSV file
csv_file_path = os.path.join(dataset_path, csv_file)

# ✅ Load the full dataset using the correct path
df = pd.read_csv(csv_file_path)

# ✅ Ensure correct column names
df.rename(columns={'generated': 'label'}, inplace=True)  # Rename 'generated' column to 'label'

# Load and balance 10000 AI + 10000 Human
# Assuming 'AI_Human.csv' is within the downloaded dataset
ai_human_csv_path = os.path.join(dataset_path, "AI_Human.csv")  # Construct the full path

In [5]:
# Assuming your data is in a CSV file
try:
    df = pd.read_csv("AI_Human.csv")  # Replace "your_dataset.csv"
except FileNotFoundError:
    print("Error: Dataset file not found.  Make sure the file is in the correct directory.")
    exit()

# Print some info
print(f"Dataset shape: {df.shape}")
print(df.head())

Dataset shape: (487235, 2)
                                                text  generated
0  Cars. Cars have been around since they became ...        0.0
1  Transportation is a large necessity in most co...        0.0
2  "America's love affair with it's vehicles seem...        0.0
3  How often do you ride in a car? Do you drive a...        0.0
4  Cars are a wonderful thing. They are perhaps o...        0.0


In [6]:
text_column = "text"  # Replace "text" with the actual column name
texts = df[text_column].astype(str).tolist()  # Convert to string and then to a list
print(f"Number of documents: {len(texts)}")

Number of documents: 487235


In [7]:
import sklearn
from sklearn.feature_extraction.text import ENGLISH_STOP_WORDS, TfidfVectorizer# Correct import
from bertopic import BERTopic
import nltk
from nltk.corpus import stopwords

In [8]:
# Download stopwords (if you haven't already)
nltk.download('stopwords')

# Define stopwords
nltk_stop_words = set(stopwords.words('english'))  # Get NLTK stop words
sklearn_stop_words = ENGLISH_STOP_WORDS  # Get scikit-learn stop words
stop_words_combined = nltk_stop_words.union(sklearn_stop_words)  # Combine them

# 5. Embedding Model (Smaller for memory)
from sentence_transformers import SentenceTransformer
embedding_model = SentenceTransformer('all-MiniLM-L6-v2') 

vectorizer_model = TfidfVectorizer(stop_words=list(stop_words_combined)) # Pass stop words to vectorizer

# 7. BERTopic Model
topic_model = BERTopic(
    embedding_model=embedding_model,
    vectorizer_model=vectorizer_model,  # Pass the customized vectorizer
    verbose=True,
    language="english",
    calculate_probabilities=False,
    low_memory=False,
)

# 7. Train the model
topics, probs = topic_model.fit_transform(texts)

# 8. Explore Topics
topic_info = topic_model.get_topic_info()
print(topic_info)

for topic in topic_info["Topic"].tolist():
    print(f"Topic {topic}: {topic_model.get_topic(topic)}")



[nltk_data] Downloading package stopwords to
[nltk_data]     /Users/thytran/nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
2025-03-25 21:15:25,946 - BERTopic - Embedding - Transforming documents to embeddings.
Batches: 100%|██████████| 15227/15227 [2:21:25<00:00,  1.79it/s]   
2025-03-25 23:37:06,291 - BERTopic - Embedding - Completed ✓
2025-03-25 23:37:06,292 - BERTopic - Dimensionality - Fitting the dimensionality reduction algorithm
OMP: Info #276: omp_set_nested routine deprecated, please use omp_set_max_active_levels instead.
2025-03-26 01:56:23,363 - BERTopic - Dimensionality - Completed ✓
2025-03-26 01:56:23,368 - BERTopic - Cluster - Start clustering the reduced embeddings
huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOK

       Topic  Count                                               Name  \
0         -1  93253           -1_dictionaries_surfing_ensures_plastics   
1          0   1926     0_mensae_pareidolia_extraterrestrial_enigmatic   
2          1   1871                   1_ekman_aus_friesen_categorizing   
3          2   1815  2_effectiveness_gerrymandering_tyranny_distrib...   
4          3   1579              3_urban_infrastructure_spaces_cycling   
...      ...    ...                                                ...   
17665  17664     10  17664_counterpart_complicating_compensating_ba...   
17666  17665     10  17665_brickandmortar_brickannmortar_hoppers_re...   
17667  17666     10                 17666_expendable_axles_curbs_urged   
17668  17667     10             17667_renewable_hydro_hydropower_fuels   
17669  17668     10                  17668_vigo_arose_graduating_discs   

                                          Representation  \
0      [dictionaries, surfing, ensures, plastics, a

In [14]:
# 9. Visualize (limit documents for memory)
#topic_model.visualize_topics()
#topic_model.visualize_documents(texts[:50000])

# 10. Save the model
topic_model.save("my_bertopic_model2", serialization="safetensors", save_embedding_model=embedding_model)